## Tutorial 5: MCA

In [ ]:
# preliminaries
%matplotlib widget
from matplotlib import pyplot as plt
import numpy as np
import scipy as sp
import scipy.misc
import pandas as pd
import os

### Question 1

In [ ]:
import pysces
m = pysces.model('lin2', '.')
m.SetQuiet()

In [ ]:
m.doSimPlot(points=100)

In [ ]:
m.doSimPlot(plot='rates',points=100)

### Question 2

In [ ]:
m.doStateShow()

### Question 3

In [ ]:
print(m.k1f, m.Vf2)
pert = 1.01
m.doState()
J_ref = m.J_v1
m.k1f *= pert
m.doState()
J_v1up = m.J_v1
m.k1f = 10.0
m.Vf2 *= pert
m.doState()
J_v2up = m.J_v1
m.Vf2 = 100.0
m.doState()
print(m.k1f, m.Vf2)
print("J_orig: ", J_ref)
print("J_v1_incr: ", J_v1up)
print("J_v2_incr: ", J_v2up)

In [ ]:
CCJ_v1 = (J_v1up - J_ref)/J_ref/(pert -1)
CCJ_v2 = (J_v2up - J_ref)/J_ref/(pert -1)
print("CCJ_v1: ", CCJ_v1)
print("CCJ_v2: ", CCJ_v2)

### Question 4

In [ ]:
print(CCJ_v1+CCJ_v2)

The FCCs don't sum exactly to one. The smaller the perturbation, the closer we get to 1 (the real value). Try it!

### Question 5

#### 5(a)

In [ ]:
def v2(Kx):
    return m.Vf2/Kx*(m.X_ss - m.P/m.Keq2)/(1 + m.X_ss/Kx + m.P/m.Kp)

In [ ]:
der = sp.misc.derivative(v2, m.Kx, dx=0.0001)
elas = der*m.Kx/v2(m.Kx)
print('derivative: ', der)
print('elasticity: ', elas)

#### 5(b)

In [ ]:
import sympy
sympy.init_printing()

In [ ]:
x, p, Kx, Kp, Vm, Keq = sympy.symbols('x p K_x K_p V_m K_eq')

In [ ]:
v2 = Vm/Kx*(x-p/Keq)/(1+x/Kx+p/Kp)

In [ ]:
v2

In [ ]:
sympy.diff(v2,Kx)

In [ ]:
elas = sympy.diff(v2,Kx)*Kx/v2
elas

In [ ]:
elas = sympy.simplify(elas)
elas

In [ ]:
elas.subs({Kx:m.Kx, Kp:m.Kp, p:m.P, x:m.X_ss})

In [ ]:
sympy.init_printing(0)

#### 5(c)

In [ ]:
m.doMca()
m.ecv2_Kx

### Question 6

In [ ]:
m.doState()
oldJ = m.J_v1
m.Kx *= 1.01
m.doState()
newJ = m.J_v1
m.Kx /= 1.01
percJ = (newJ-oldJ)/oldJ*100
print(percJ)

The system flux changes by -0.0357, which is about half of the change that we see for v2 in isolation (-0.069). At complete control of the flux for v2 ($C^J_{v2}=1$) we would have expected a change of $R^J_{Kx}=C^J_{v2}\varepsilon^{v2}_{Kx}=1\cdot(-0.069)=-0.069$. But we calculated $C^J_{v2}=0.52$, therefore $R^J_{Kx}=0.52\times\varepsilon^{v2}_{Kx}$.

### Question 7

In [ ]:
sympy.init_printing(1)
from sympy.abc import epsilon

In [ ]:
CJ1, CJ2, ev1x, ev2x = sympy.symbols('C^J_1 C^J_2 epsilon^v1_x epsilon^v2_x')

In [ ]:
eq1 = sympy.Eq(CJ1+CJ2, 1)
eq2 = sympy.Eq(CJ1*ev1x+CJ2*ev2x, 0)

In [ ]:
sympy.solve([eq1, eq2], [CJ1, CJ2])

In [ ]:
sympy.init_printing(0)

### Question 8

In [ ]:
# elasticities from PySCeS
m.doMca()
CJ1 = m.ecv2_X/(m.ecv2_X-m.ecv1_X)
CJ2 = -m.ecv1_X/(m.ecv2_X-m.ecv1_X)
print('CJ1: ', CJ1)
print('CJ2: ', CJ2)
print('sum: ', CJ1+CJ2)

In [ ]:
# control coefficients from PySCeS directly
print(m.ccJv1_v1)
print(m.ccJv1_v2)
print(m.ccJv1_v1 + m.ccJv1_v2)

### Question 9

In [ ]:
m.ccJv2_v1*m.ecv1_X + m.ccJv2_v2*m.ecv2_X

In [ ]:
m.J_v1 

In [ ]:
m.J_v2